## 1. Churn Feature Engineering Pyspark

In [97]:
from hops import featurestore
from pyspark.sql.types import DoubleType
from pyspark.ml import Pipeline
from pyspark.ml.feature import OneHotEncoderEstimator, StringIndexer, VectorAssembler, StandardScaler
from pyspark.ml.linalg import Vectors

### 1.1 Data

In [98]:
connector = featurestore.get_storage_connector("redshift_spark_connector",featurestore=featurestore.project_featurestore())
connection_string = connector.connection_string
db_pass = connector.arguments

In [99]:
df = (spark.read.
      format("jdbc").
      option("driver", "com.amazon.redshift.jdbc42.Driver").
      option("url", connection_string).
      option("dbtable", "demo").
      option("user", "hopsusername").
      option("password", db_pass).
      load())


In [100]:
df = df.toDF('customer_id', 'gender', 'senior_citizen', 'partner', 'dependents',
       'tenure', 'phone_service', 'multiple_lines', 'internet_service',
       'online_security', 'online_backup', 'device_protection', 'tech_support',
       'streaming_tv', 'streaming_movies', 'contract', 'paperless_billing',
       'payment_method', 'monthly_charges', 'total_charges', 'churn')

df = df.withColumn("tenure",df.tenure.cast(DoubleType()))

### 1.2 Data Manipulation and Processing

In [101]:
categoricalColumns = ['gender','senior_citizen','partner','dependents','phone_service','multiple_lines','internet_service', 'online_security', 'online_backup', 'device_protection', 'tech_support',
                      'streaming_tv', 'streaming_movies', 'contract', 'paperless_billing','payment_method']

numericalColumns = ['tenure', 'monthly_charges', 'total_charges']
df = df.fillna(0, subset=numericalColumns )

stages = [] # stages in our Pipeline
out_cat_col = []
for categoricalCol in categoricalColumns:
    # Category Indexing with StringIndexer
    stringIndexer = StringIndexer(inputCol=categoricalCol, outputCol=categoricalCol + "_Index")
    stages += [stringIndexer]
    out_cat_col += [categoricalCol + "_Index"]

assembler = VectorAssembler(
    inputCols=numericalColumns,
    outputCol="numFeatures")
stages += [assembler]

# scaling numericalColumns
standardScaler = StandardScaler(inputCol="numFeatures", outputCol="scaledFeatures",withStd=True, withMean=False)
stages += [standardScaler]
    
# Convert label into label indices using the StringIndexer
label_stringIdx = StringIndexer(inputCol="churn", outputCol="label")
stages += [label_stringIdx]

In [102]:
# Create a Pipeline.
pipeline = Pipeline(stages=stages)
# Run the feature transformations.
#  - fit() computes feature statistics as needed.
#  - transform() actually transforms the features.
pipelineModel = pipeline.fit(df)
dataset = pipelineModel.transform(df)

In [104]:
def extract(row):
    col_list = []
    col_list.append("label")
    for x in out_cat_col:
        col_list.append(row[x])
    return tuple(col_list) + tuple(row["scaledFeatures"].toArray().tolist())

telcom_churn_features = dataset.rdd.map(extract).toDF(["label" ]+ categoricalColumns + numericalColumns)

### 1.4 Create FeatureGroups

In [94]:
featurestore.create_featuregroup(
    telcom_churn_features,
    "telcom_featuregroup",
    description="Telecom churn prediction feature group", 
    online=True,
    descriptive_statistics=True,
    feature_correlation=True,
    feature_histograms=True,
    cluster_analysis=True
)

computing descriptive statistics for : telcom_churn_features, version: 1
computing feature correlation for: telcom_churn_features, version: 1
computing feature histograms for: telcom_churn_features, version: 1
computing cluster analysis for: telcom_churn_features, version: 1
Registering feature metadata...
Registering feature metadata... [COMPLETE]
Writing feature data to offline feature group (Hive)...
Running sql: use demo_featurestore_davit000_featurestore against offline feature store
Writing feature data to offline feature group (Hive)... [COMPLETE]
Feature group created successfully